In [1]:
import random

import torch 
import numpy as np
import pandas as pd

device = "cuda" if torch.cuda.is_available() else "cpu"
print(device)

cpu


In [2]:
text_chunks_and_embeddings = pd.read_csv('C:\\Users\\hp probook\\Desktop\\RAG_Project\\data_preprocessing\\bdd.csv')

text_chunks_and_embeddings['embeddings'] = text_chunks_and_embeddings['embeddings'].apply(lambda x : np.fromstring(x.strip("[]"), sep=', '))

# text_chunks_and_embeddings['embeddings'] = text_chunks_and_embeddings['embeddings'].apply(lambda x: np.fromstring(x[1:-1], sep=' '))

pages_and_chunks = text_chunks_and_embeddings.to_dict(orient= "records")
pages_and_chunks

[{'page_number': 1,
  'sentence_chunk': '1  Préambule  Après onze années en tant que chargé de cours du module « Bases De Données » à  l’Ecole Supérieure d’Informatique, je me rappelle toujours du coup de fil de Mr Medjaoui  (Directeur des études de l’époque) me demandant d’assurer ce cours pour les étudiants de  3ème année option « Systèmes d’Information ». A peine recruté, je me retrouve comme  chargé de cours devant 150 étudiants, tous assoiffés de savoir et qui en demandaient toujours  d’avantage. N’ayant pas une grande expérience en pédagogie, ce fut uniquement mon expérience  professionnelle en tant que développeur et administrateur de bases de données qui a poussé  le DE à me désigner pour cette tâche. J’ai commencé alors à chercher des supports de cours  pour m’imprégner du module et préparer mes leçons, mais, hélas, je n’ai pas trouvé ne serait- ce qu’un brouillon. Je me suis alors réfugié à la bibliothèque de l’école où j’ai pratiquement  dévoré tous les livres qui parlaient 

In [3]:
embeddings = torch.tensor(np.stack(text_chunks_and_embeddings['embeddings'].tolist(), axis=0))
embeddings.shape

torch.Size([509, 768])

In [5]:
from sentence_transformers import SentenceTransformer, util

embedding_model = SentenceTransformer(model_name_or_path="all-mpnet-base-v2", device= device)

### steps:
* define a query string 
* turn the query into an embedding vector 
* perform the similarity search by using teh cosine similarity function between the chunks embedding and the query embedding
* choose the 3 chunks with highest degree of similarity   

In [11]:
#define a query 
query = "Définition  Le produit cartésien de deux relations R1 et R2"
print(f"query: {query}")

embeded_query = embedding_model.encode(query, convert_to_tensor=True).to('cpu')
embeded_query

from time import perf_counter as timer 

dot_scores = util.dot_score(a=embeded_query.float(), b=embeddings.float())[0]

top_values = torch.topk(dot_scores, k=5)

print(top_values)


query: Définition  Le produit cartésien de deux relations R1 et R2
torch.return_types.topk(
values=tensor([0.8626, 0.7535, 0.7281, 0.6867, 0.6765]),
indices=tensor([295, 299, 322, 196, 195]))


In [ ]:
"""
faiss library to create vector database
and ann methode to seacrh the relevent passages 
cosine similarity is just the dot product of values already normalized (L2 norm : la racine de (la somme des ( valeurs au carré))), and it's favored to use cosine similarity then the dot product when we do semantic search

mixedbread rerank model used to rerank the top k values 
falshattention to speed up the attention mechanism of transformers and generating the token of our llm
"""

"\nfaiss library to create vector database\nand ann methode to seacrh the relevent passages \ncosine similarity is just the dot product of values already normalized (L2 norm : la racine de (la somme des ( valeurs au carré))), and it's favored to use cosine similarity then the dot product when we do semantic search\n\nmixedbread rerank model used to rerank the top k values \n"

In [1]:
for value, index in zip(top_values.values.tolist(), top_values.indices.tolist()):
    print(f"score:  {value}")
    print(f"text: {pages_and_chunks[index]['sentence_chunk']}")
    print(f"page:  {pages_and_chunks[index]['page_number']}")
    print('\n')
    # print(f"value : {value}")
    # print(f"index : {index}")

NameError: name 'top_values' is not defined

### Functionazing the semantic search pipeline:

In [102]:
def retrieval_semantic_search(query: str,
                    embeddings: torch.tensor,
                    top_n: int,
                    model: SentenceTransformer= embedding_model):
    
    query_embeded = model.encode(query,convert_to_tensor=True)

    #model encode return embeddings already normalized
    dot_scores = util.dot_score(query_embeded.float(),embeddings.float())
    top_scores_indexs = torch.topk(dot_scores, k=top_n)

    return top_scores_indexs

def top_scores_indexs(query: str,
                      embeddings: torch.tensor,
                      top_n: int,
                      model: SentenceTransformer= embedding_model):

    top_scores_indexs = retrieval_semantic_search(query,
                          embeddings = embeddings,
                          top_n=top_n)
    #printing them
    for value, index in zip(top_scores_indexs.values.tolist()[0], top_scores_indexs.indices.tolist()[0]):
        print(f"score:  {value}")
        print(f"text: {pages_and_chunks[index]['sentence_chunk']}")
        print(f"page:  {pages_and_chunks[index]['page_number']}")
        print('\n')

In [105]:
top_scores_indexs(query="explique la clause SELECT",
                          embeddings = embeddings,
                          top_n=5)

score:  0.5488355159759521
text: Les expressions SQL  Les expressions SQL permettent d’enrichir les clauses de sélection de la clause  SELECT et les conditions de la clause WHERE.
page:  138


score:  0.5384021997451782
text: Une grande partie  de ce chapitre est consacrée à l’interrogation des données avec la clause  SELECT.
page:  127


score:  0.48965808749198914
text: Groupement de lignes  Les expressions utilisées dans la clause Select et Where font des comparaisons entre  les valeurs des colonnes d’une ligne donnée.
page:  139


score:  0.4802717864513397
text: Cette opération est surtout utilisée dans d’autres opérations.
page:  105


score:  0.4510614275932312
text: On peut utiliser l’opérateur IN.
page:  139


